# Porto Taxi Analytical Notebook
This notebook runs reusable SQL queries against the Porto taxi MySQL database and prints tabulated outputs for the assignment questions.

## 1. Notebook Configuration
Import core libraries and set display preferences for consistent tabulated outputs.

In [52]:
# Core libraries
import os
from pathlib import Path
from typing import Callable, Optional

import pandas as pd
from tabulate import tabulate

# Optional: load environment variables from .env if present
try:
    from dotenv import load_dotenv
    load_dotenv()
except ModuleNotFoundError:
    pass

# Display preferences
pd.set_option("display.max_rows", 50)
pd.set_option("display.max_columns", 50)
pd.set_option("display.float_format", lambda x: f"{x:,.2f}")

DATA_DIR = Path.cwd()
print(f"Working directory: {DATA_DIR}")

Working directory: /Users/almax/Documents/NTNU/25h/very_large_data_volumes/portodata/queries


## 2. Database Connection Utilities
Create a SQLAlchemy engine using the environment-provided MySQL credentials and test the connection.

In [53]:
# from sqlalchemy import create_engine, text
from pathlib import Path
import sys
PROJECT_ROOT = DATA_DIR
if str(PROJECT_ROOT) not in sys.path:
    sys.path.insert(0, str(PROJECT_ROOT))

from sqlalchemy import create_engine, text

DB_HOST = os.getenv("DB_HOST", "127.0.0.1")
DB_PORT = int(os.getenv("DB_PORT", os.getenv("PORT", 3306)))
DB_NAME = os.getenv("DB_DATABASE", "porto")
DB_USER = os.getenv("DB_USER", "root")
DB_PASSWORD = os.getenv("DB_PASSWORD", "password")

engine_url = (
    f"mysql+mysqlconnector://{DB_USER}:{DB_PASSWORD}@{DB_HOST}:{DB_PORT}/{DB_NAME}"
)
engine = create_engine(engine_url)
# connector = DbConnector()
# cursor = connector.cursor
# ensure_schema(cursor)
# if connector.db_connection:
#     connector.db_connection.commit()

with engine.connect() as conn:
    db_version = conn.execute(text("SELECT VERSION()"))
    print(f"Connected to MySQL version: {db_version.scalar()}")
    current_db = conn.execute(text("SELECT DATABASE()"))
    print(f"Using database: {current_db.scalar()}")

Connected to MySQL version: 9.4.0
Using database: porto2


## 3. Reusable Query Execution Helper with Tabulate
Define a helper to run SQL, return the result as a DataFrame, and print it using tabulate.

In [54]:
def run_query(sql: str, params: Optional[dict] = None, title: Optional[str] = None, postprocess: Optional[Callable[[pd.DataFrame], pd.DataFrame]] = None) -> pd.DataFrame:
    """Execute SQL, return a DataFrame, and print tabulated output."""
    if title:
        print(title)
        print("-" * len(title))
    with engine.connect() as conn:
        df = pd.read_sql(text(sql), conn, params=params)
    if postprocess is not None:
        df = postprocess(df)
    if df.empty:
        print("No rows returned.")
        return df
    print(tabulate(df, headers=df.columns, tablefmt="grid", showindex=False))
    print()
    print(tabulate(df, headers=df.columns, tablefmt="plain", showindex=False))
    return df


def format_minutes(seconds_series: pd.Series) -> pd.Series:
    """Convert seconds to minutes with two decimal places."""
    return seconds_series / 60.0


def format_kilometers(meters_series: pd.Series) -> pd.Series:
    """Convert meters to kilometers with two decimal places."""
    return meters_series / 1000.0

## 4. Question 1 - Core Dataset Counts
Summaries of unique taxis, trips, and GPS points stored in the warehouse tables.

In [55]:
q1_sql = """
SELECT 'Distinct taxis' AS metric, COUNT(DISTINCT taxi_id) AS value FROM trips
UNION ALL
SELECT 'Trips' AS metric, COUNT(*) AS value FROM trips
UNION ALL
SELECT 'Trip points' AS metric, COUNT(*) AS value FROM trip_points
"""

q1_df = run_query(q1_sql, title="Question 1 - Core Dataset Counts")

Question 1 - Core Dataset Counts
--------------------------------
+----------------+----------+
| metric         |    value |
+================+==========+
| Distinct taxis |      448 |
+----------------+----------+
| Trips          |  1710589 |
+----------------+----------+
| Trip points    | 83409283 |
+----------------+----------+

metric             value
Distinct taxis       448
Trips            1710589
Trip points     83409283


## 5. Question 2 - Average Trips per Taxi
Compute the mean trip count per taxi to understand fleet utilisation.

In [56]:
q2_sql = """
SELECT COUNT(*) / COUNT(DISTINCT taxi_id) AS avg_trips_per_taxi
FROM trips
"""

q2_df = run_query(q2_sql, title="Question 2 - Average Trips per Taxi")

Question 2 - Average Trips per Taxi
-----------------------------------
+----------------------+
|   avg_trips_per_taxi |
+======================+
|              3818.28 |
+----------------------+

  avg_trips_per_taxi
             3818.28


## 6. Question 3 - 20 Busiest Taxis
Rank taxis by trip volume to find the most active drivers.

In [57]:
q3_sql = """
SELECT taxi_id, COUNT(*) AS trip_count
FROM trips
GROUP BY taxi_id
ORDER BY trip_count DESC
LIMIT 20
"""


def _postprocess_q3(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    converted["taxi_id"] = converted["taxi_id"].astype(int).astype(str)
    return converted


q3_df = run_query(q3_sql, title="Question 3 - Top 20 Taxis by Trip Count", postprocess=_postprocess_q3)

Question 3 - Top 20 Taxis by Trip Count
---------------------------------------
+-----------+--------------+
|   taxi_id |   trip_count |
+===========+==============+
|  20000080 |        10731 |
+-----------+--------------+
|  20000403 |         9237 |
+-----------+--------------+
|  20000066 |         8443 |
+-----------+--------------+
|  20000364 |         7821 |
+-----------+--------------+
|  20000483 |         7729 |
+-----------+--------------+
|  20000129 |         7608 |
+-----------+--------------+
|  20000307 |         7497 |
+-----------+--------------+
|  20000621 |         7276 |
+-----------+--------------+
|  20000089 |         7266 |
+-----------+--------------+
|  20000424 |         7176 |
+-----------+--------------+
|  20000492 |         7171 |
+-----------+--------------+
|  20000529 |         6937 |
+-----------+--------------+
|  20000616 |         6924 |
+-----------+--------------+
|  20000678 |         6538 |
+-----------+--------------+
|  20000372 |        

## 7a. Question 4a - Dominant Call Type per Busy Taxi
For the busiest taxis, identify the call type they served most frequently.

In [58]:
q4_sql = """
WITH ranked AS (
    SELECT
        t.taxi_id,
        t.call_type,
        ct.description AS call_type_description,
        COUNT(*) AS trip_count,
        ROW_NUMBER() OVER (PARTITION BY t.taxi_id ORDER BY COUNT(*) DESC) AS rn
    FROM trips t
    LEFT JOIN call_types ct ON ct.call_type = t.call_type
    GROUP BY t.taxi_id, t.call_type, ct.description
)
SELECT
    taxi_id,
    call_type,
    COALESCE(call_type_description, 'Unknown') AS call_type_description,
    trip_count
FROM ranked
WHERE rn = 1
ORDER BY trip_count DESC
LIMIT 20
"""

q4_df = run_query(q4_sql, title="Question 4 - Dominant Call Type for Busiest Taxis")

Question 4 - Dominant Call Type for Busiest Taxis
-------------------------------------------------
+-----------+-------------+-------------------------------+--------------+
|   taxi_id | call_type   | call_type_description         |   trip_count |
+===========+=============+===============================+==============+
|  20000080 | C           | Picked up from a taxi stand   |         8362 |
+-----------+-------------+-------------------------------+--------------+
|  20000066 | C           | Picked up from a taxi stand   |         5064 |
+-----------+-------------+-------------------------------+--------------+
|  20000403 | C           | Picked up from a taxi stand   |         4758 |
+-----------+-------------+-------------------------------+--------------+
|  20000364 | C           | Picked up from a taxi stand   |         4563 |
+-----------+-------------+-------------------------------+--------------+
|  20000304 | C           | Picked up from a taxi stand   |         3995 |


## 7b. Question 4b - Call Type Duration, Distance, and Time-Band Share
For each call type, compute average duration and distance plus the share of trips starting in four time bands (00–06, 06–12, 12–18, 18–24).

In [72]:
q4b_sql = """
WITH banded AS (
    SELECT
        t.call_type,
        ct.description AS call_type_description,
        t.duration_seconds,
        t.total_distance_m,
        CASE
            WHEN HOUR(t.start_time) < 6 THEN '00-06'
            WHEN HOUR(t.start_time) < 12 THEN '06-12'
            WHEN HOUR(t.start_time) < 18 THEN '12-18'
            ELSE '18-24'
        END AS time_band
    FROM trips t
    LEFT JOIN call_types ct ON ct.call_type = t.call_type
    WHERE t.is_valid = TRUE AND t.duration_seconds IS NOT NULL AND t.total_distance_m IS NOT NULL
), aggregated AS (
    SELECT
        call_type,
        COALESCE(call_type_description, 'Unknown') AS call_type_description,
        COUNT(*) AS trip_count,
        AVG(duration_seconds) AS avg_duration_seconds,
        AVG(total_distance_m) AS avg_distance_m,
        SUM(CASE WHEN time_band = '00-06' THEN 1 ELSE 0 END) AS band_00_06,
        SUM(CASE WHEN time_band = '06-12' THEN 1 ELSE 0 END) AS band_06_12,
        SUM(CASE WHEN time_band = '12-18' THEN 1 ELSE 0 END) AS band_12_18,
        SUM(CASE WHEN time_band = '18-24' THEN 1 ELSE 0 END) AS band_18_24
    FROM banded
    GROUP BY call_type, call_type_description
)
SELECT
    call_type,
    call_type_description,
    trip_count,
    avg_duration_seconds,
    avg_distance_m,
    band_00_06 / trip_count AS share_00_06,
    band_06_12 / trip_count AS share_06_12,
    band_12_18 / trip_count AS share_12_18,
    band_18_24 / trip_count AS share_18_24
FROM aggregated
ORDER BY trip_count DESC
"""


def _postprocess_q4b(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    converted["avg_duration_minutes"] = format_minutes(converted["avg_duration_seconds"]).round(2)
    converted["avg_distance_km"] = format_kilometers(converted["avg_distance_m"]).round(2)
    for col in ["share_00_06", "share_06_12", "share_12_18", "share_18_24"]:
        converted[col] = (converted[col] * 100).round(2)
    return converted[[
        "call_type",
        "call_type_description",
        "trip_count",
        "avg_duration_minutes",
        "avg_distance_km",
        "share_00_06",
        "share_06_12",
        "share_12_18",
        "share_18_24",
    ]]


q4b_df = run_query(q4b_sql, title="Question 4b - Call Type Duration, Distance, and Time-Band Share", postprocess=_postprocess_q4b)

Question 4b - Call Type Duration, Distance, and Time-Band Share
---------------------------------------------------------------
+-------------+-------------------------------+--------------+------------------------+-------------------+---------------+---------------+---------------+---------------+
| call_type   | call_type_description         |   trip_count |   avg_duration_minutes |   avg_distance_km |   share_00_06 |   share_06_12 |   share_12_18 |   share_18_24 |
+=============+===============================+==============+========================+===================+===============+===============+===============+===============+
| B           | Hailed directly on the street |       806926 |                  11.21 |              5.08 |         12.23 |         30.13 |         34.49 |         23.16 |
+-------------+-------------------------------+--------------+------------------------+-------------------+---------------+---------------+---------------+---------------+
| C         

## 8. Question 5 - Taxis with Most Driving Hours
Compare taxis by cumulative driving hours and distance covered.

In [66]:
q5_sql = """
SELECT
    taxi_id,
    SUM(duration_seconds) AS total_duration_seconds,
    SUM(total_distance_m) AS total_distance_m
FROM trips
WHERE is_valid = TRUE
GROUP BY taxi_id
ORDER BY total_duration_seconds DESC
LIMIT 20
"""


def _postprocess_q5(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    converted["total_hours"] = (converted["total_duration_seconds"] / 3600.0).round(2)
    converted["total_distance_km"] = (converted["total_distance_m"] / 1000.0).round(2)
    converted["taxi_id"] = converted["taxi_id"].astype(int).astype(str)
    return converted[["taxi_id", "total_hours", "total_distance_km"]]


q5_df = run_query(q5_sql, title="Question 5 - Taxis with Most Driving Hours", postprocess=_postprocess_q5)

Question 5 - Taxis with Most Driving Hours
------------------------------------------
+-----------+---------------+---------------------+
|   taxi_id |   total_hours |   total_distance_km |
+===========+===============+=====================+
|  20000904 |       1841.18 |             58459.2 |
+-----------+---------------+---------------------+
|  20000129 |       1646.89 |             36193.1 |
+-----------+---------------+---------------------+
|  20000307 |       1585.38 |             39782.4 |
+-----------+---------------+---------------------+
|  20000529 |       1507.27 |             42386.1 |
+-----------+---------------+---------------------+
|  20000483 |       1397.51 |             36147.7 |
+-----------+---------------+---------------------+
|  20000276 |       1393.68 |             45645.2 |
+-----------+---------------+---------------------+
|  20000372 |       1387.05 |             40676.1 |
+-----------+---------------+---------------------+
|  20000436 |       1369.09 | 

## 9. Question 6 - Trips Passing Near Porto City Hall
List trips whose GPS traces pass within ~150m of Porto City Hall.

In [60]:
q6_sql = """
SELECT DISTINCT
    t.trip_id,
    t.taxi_id,
    t.start_time,
    ROUND(t.total_distance_m / 1000.0, 2) AS total_distance_km
FROM trip_points tp
JOIN trips t ON t.trip_id = tp.trip_id
WHERE tp.longitude BETWEEN (-8.62911 - 0.0012) AND (-8.62911 + 0.0012)
  AND tp.latitude BETWEEN (41.15794 - 0.0009) AND (41.15794 + 0.0009)
ORDER BY t.start_time
LIMIT 50
"""

q6_df = run_query(q6_sql, title="Question 6 - Trips Passing Near Porto City Hall")

Question 6 - Trips Passing Near Porto City Hall
-----------------------------------------------
+---------------------+-----------+---------------------+---------------------+
|             trip_id |   taxi_id | start_time          |   total_distance_km |
+=====================+===========+=====================+=====================+
| 1372636896620000360 |  20000360 | 2013-07-01 00:01:36 |                8.51 |
+---------------------+-----------+---------------------+---------------------+
| 1372636956620000167 |  20000167 | 2013-07-01 00:02:36 |                3.75 |
+---------------------+-----------+---------------------+---------------------+
| 1372637247620000067 |  20000067 | 2013-07-01 00:07:27 |                2.9  |
+---------------------+-----------+---------------------+---------------------+
| 1372637423620000341 |  20000341 | 2013-07-01 00:10:23 |                7.84 |
+---------------------+-----------+---------------------+---------------------+
| 1372637610620000497 | 

## 10. Question 7 - Invalid or Flagged Trips
Break down trips marked as invalid, outliers, or with missing data.

In [61]:
q7_sql = """
SELECT 'Trips flagged with missing_data' AS issue, COUNT(*) AS trip_count
FROM trips
WHERE missing_data = TRUE
UNION ALL
SELECT 'Trips marked as outliers' AS issue, COUNT(*) AS trip_count
FROM trips
WHERE is_outlier = TRUE
UNION ALL
SELECT 'Trips considered invalid' AS issue, COUNT(*) AS trip_count
FROM trips
WHERE is_valid = FALSE
UNION ALL
SELECT 'Valid, non-outlier trips' AS issue, COUNT(*) AS trip_count
FROM trips
WHERE is_valid = TRUE AND is_outlier = FALSE
"""

q7_df = run_query(q7_sql, title="Question 7 - Invalid or Flagged Trips")

Question 7 - Invalid or Flagged Trips
-------------------------------------
+---------------------------------+--------------+
| issue                           |   trip_count |
+=================================+==============+
| Trips flagged with missing_data |           10 |
+---------------------------------+--------------+
| Trips marked as outliers        |         1582 |
+---------------------------------+--------------+
| Trips considered invalid        |        45238 |
+---------------------------------+--------------+
| Valid, non-outlier trips        |      1665351 |
+---------------------------------+--------------+

issue                              trip_count
Trips flagged with missing_data            10
Trips marked as outliers                 1582
Trips considered invalid                45238
Valid, non-outlier trips              1665351


## 11. Question 8 - Busiest Hours of the Day
Identify peak operating hours based on trip start times.

In [67]:
q8_sql = """
SELECT
    HOUR(start_time) AS start_hour,
    COUNT(*) AS trip_count,
    ROUND(100.0 * COUNT(*) / SUM(COUNT(*)) OVER (), 2) AS pct_of_trips
FROM trips
WHERE is_valid = TRUE
GROUP BY start_hour
ORDER BY trip_count DESC
"""


def _postprocess_q8(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    converted["hour_window"] = converted["start_hour"].apply(lambda h: f"{int(h):02d}:00-{int(h):02d}:59")
    cols = ["start_hour", "hour_window", "trip_count", "pct_of_trips"]
    return converted[cols]


q8_df = run_query(q8_sql, title="Question 8 - Busiest Hours of the Day", postprocess=_postprocess_q8)

Question 8 - Busiest Hours of the Day
-------------------------------------
+--------------+---------------+--------------+----------------+
|   start_hour | hour_window   |   trip_count |   pct_of_trips |
+==============+===============+==============+================+
|            9 | 09:00-09:59   |        96276 |           5.78 |
+--------------+---------------+--------------+----------------+
|            8 | 08:00-08:59   |        90790 |           5.45 |
+--------------+---------------+--------------+----------------+
|           14 | 14:00-14:59   |        90081 |           5.41 |
+--------------+---------------+--------------+----------------+
|           10 | 10:00-10:59   |        89460 |           5.37 |
+--------------+---------------+--------------+----------------+
|           15 | 15:00-15:59   |        88507 |           5.31 |
+--------------+---------------+--------------+----------------+
|           13 | 13:00-13:59   |        86318 |           5.18 |
+-------------

## 12. Question 9 - Midnight Crossing Trips
Identify trips that start on one calendar day and finish on the next day.

In [69]:
q9_sql = """
SELECT
    trip_id,
    taxi_id,
    start_time,
    end_time,
    duration_seconds,
    total_distance_m
FROM trips
WHERE end_time IS NOT NULL
  AND DATE(start_time) <> DATE(end_time)
  AND DATEDIFF(end_time, start_time) = 1
ORDER BY start_time
"""


def _postprocess_q9(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    if converted.empty:
        return converted
    converted["taxi_id"] = converted["taxi_id"].astype(int).astype(str)
    converted["duration_minutes"] = format_minutes(converted["duration_seconds"]).round(2)
    converted["total_distance_km"] = format_kilometers(converted["total_distance_m"]).round(2)
    return converted[[
        "trip_id",
        "taxi_id",
        "start_time",
        "end_time",
        "duration_minutes",
        "total_distance_km",
    ]]


q9_df = run_query(q9_sql, title="Question 9 - Midnight Crossing Trips", postprocess=_postprocess_q9)

Question 9 - Midnight Crossing Trips
------------------------------------
+---------------------+-----------+---------------------+---------------------+--------------------+---------------------+
|             trip_id |   taxi_id | start_time          | end_time            |   duration_minutes |   total_distance_km |
+=====================+===========+=====================+=====================+====================+=====================+
| 1372722134620000435 |  20000435 | 2013-07-01 23:42:14 | 2013-07-02 00:02:44 |              20.5  |               14.41 |
+---------------------+-----------+---------------------+---------------------+--------------------+---------------------+
| 1372722457620000569 |  20000569 | 2013-07-01 23:47:37 | 2013-07-02 00:28:22 |              40.75 |               13.27 |
+---------------------+-----------+---------------------+---------------------+--------------------+---------------------+
| 1372722471620000540 |  20000540 | 2013-07-01 23:47:51 | 2013-07

## 13. Question 10 - Circular Trips Within 50 m
List trips whose start and end coordinates are within 50 metres of each other.

In [70]:
q10_sql = """
SELECT
    trip_id,
    taxi_id,
    start_time,
    end_time,
    total_distance_m,
    start_latitude,
    start_longitude,
    end_latitude,
    end_longitude,
    2 * 6371000 * ASIN(SQRT(
        POWER(SIN(RADIANS(end_latitude - start_latitude) / 2), 2) +
        COS(RADIANS(start_latitude)) * COS(RADIANS(end_latitude)) *
        POWER(SIN(RADIANS(end_longitude - start_longitude) / 2), 2)
    )) AS start_end_distance_m
FROM trips
WHERE is_valid = TRUE
  AND start_latitude IS NOT NULL
  AND start_longitude IS NOT NULL
  AND end_latitude IS NOT NULL
  AND end_longitude IS NOT NULL
HAVING start_end_distance_m <= 50
ORDER BY start_end_distance_m ASC
LIMIT 100
"""


def _postprocess_q10(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    if converted.empty:
        return converted
    converted["taxi_id"] = converted["taxi_id"].astype(int).astype(str)
    converted["total_distance_km"] = format_kilometers(converted["total_distance_m"]).round(2)
    converted["start_end_distance_m"] = converted["start_end_distance_m"].round(2)
    return converted[[
        "trip_id",
        "taxi_id",
        "start_time",
        "end_time",
        "total_distance_km",
        "start_end_distance_m",
    ]]


q10_df = run_query(q10_sql, title="Question 10 - Circular Trips Within 50 m", postprocess=_postprocess_q10)

Question 10 - Circular Trips Within 50 m
----------------------------------------
+---------------------+-----------+---------------------+---------------------+---------------------+------------------------+
|             trip_id |   taxi_id | start_time          | end_time            |   total_distance_km |   start_end_distance_m |
+=====================+===========+=====================+=====================+=====================+========================+
| 1377620100620000527 |  20000527 | 2013-08-27 16:15:00 | 2013-08-27 16:16:00 |                0    |                      0 |
+---------------------+-----------+---------------------+---------------------+---------------------+------------------------+
| 1375639900620000239 |  20000239 | 2013-08-04 18:11:40 | 2013-08-04 18:21:55 |                0.08 |                      0 |
+---------------------+-----------+---------------------+---------------------+---------------------+------------------------+
| 1391230743620000288 |  2000

## 14. Question 11 - Average Idle Time Between Trips
Compute each taxi's average idle time between consecutive trips and show the top 20.

In [71]:
q11_sql = """
WITH ordered AS (
    SELECT
        taxi_id,
        trip_id,
        start_time,
        end_time,
        LAG(end_time) OVER (PARTITION BY taxi_id ORDER BY start_time) AS prev_end_time
    FROM trips
    WHERE is_valid = TRUE AND end_time IS NOT NULL
), deltas AS (
    SELECT
        taxi_id,
        trip_id,
        start_time,
        prev_end_time,
        TIMESTAMPDIFF(SECOND, prev_end_time, start_time) AS idle_seconds
    FROM ordered
    WHERE prev_end_time IS NOT NULL
)
SELECT
    taxi_id,
    COUNT(*) AS gap_count,
    AVG(idle_seconds) AS avg_idle_seconds,
    MAX(idle_seconds) AS max_idle_seconds,
    MIN(idle_seconds) AS min_idle_seconds
FROM deltas
WHERE idle_seconds >= 0
GROUP BY taxi_id
HAVING gap_count > 0
ORDER BY avg_idle_seconds DESC
LIMIT 20
"""


def _postprocess_q11(df: pd.DataFrame) -> pd.DataFrame:
    converted = df.copy()
    if converted.empty:
        return converted
    converted["taxi_id"] = converted["taxi_id"].astype(int).astype(str)
    for col in ["avg_idle_seconds", "max_idle_seconds", "min_idle_seconds"]:
        converted[f"{col.replace('_seconds', '')}_minutes"] = format_minutes(converted[col]).round(2)
    return converted[[
        "taxi_id",
        "gap_count",
        "avg_idle_minutes",
        "max_idle_minutes",
        "min_idle_minutes",
    ]]


q11_df = run_query(q11_sql, title="Question 11 - Average Idle Time Between Trips", postprocess=_postprocess_q11)

Question 11 - Average Idle Time Between Trips
---------------------------------------------
+-----------+-------------+--------------------+--------------------+--------------------+
|   taxi_id |   gap_count |   avg_idle_minutes |   max_idle_minutes |   min_idle_minutes |
+===========+=============+====================+====================+====================+
|  20000941 |           3 |          104797    |          314387    |               1.1  |
+-----------+-------------+--------------------+--------------------+--------------------+
|  20000969 |          24 |           16924.3  |          259181    |               2.13 |
+-----------+-------------+--------------------+--------------------+--------------------+
|  20000510 |         618 |             804.97 |           52878.1  |               0.08 |
+-----------+-------------+--------------------+--------------------+--------------------+
|  20000312 |         580 |             788.27 |           48824.4  |               0.12 